In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Install Required Libraries
Run this cell to install the necessary packages. CLIP requires PyTorch, and we'll use scikit-learn for clustering, along with Pillow for image loading and matplotlib for visualization.

In [ ]:
!pip install ftfy regex tqdm
!pip install git+https://github.com/openai/CLIP.git
!pip install scikit-learn matplotlib pillow umap-learn  # UMAP is optional for 2D visualization

Load Images and Extract CLIP Embeddings
Replace `/path/to/your/images` with your image directory (e.g., `/content/uploaded_images` for uploaded files or `/content/drive/MyDrive/images` for Drive).

This code loads all images (supports JPG, PNG, etc.), preprocesses them, and extracts 512-dimensional embeddings using the ViT-B/32 CLIP model.

In [ ]:
!pip install open_clip_torch  # Install if needed

import open_clip
import torch
from PIL import Image
import numpy as np
import os

# Configuration
image_dir = '/content/'
device = "cuda" if torch.cuda.is_available() else "cpu"
model_name = "ViT-B-32-quickgelu"  # Or "laion2b_s34b_b79k" for fine-tuned

# Load OpenCLIP model
model, _, preprocess = open_clip.create_model_and_transforms(model_name, pretrained="laion400m_e32")  # Use 'laion2b_s34b_b88k' for fine-tune
model.to(device)

# Load images and extract embeddings
embeddings = []
image_names = []
for filename in os.listdir(image_dir):
    if filename.lower().endswith(('.png', '.jpg', '.jpeg')):
        img_path = os.path.join(image_dir, filename)
        try:
            image = preprocess(Image.open(img_path)).unsqueeze(0).to(device)
            with torch.no_grad():
                embedding = model.encode_image(image)
            embeddings.append(embedding.cpu().numpy().flatten())
            image_names.append(filename)
            print(f"Processed: {filename}")
        except Exception as e:
            print(f"Error: {e}")

embeddings = np.array(embeddings)
print(f"Extracted embeddings for {len(embeddings)} images. Shape: {embeddings.shape}")

Perform Clustering
We'll use K-Means clustering on the embeddings. You can choose the number of clusters (`n_clusters`) based on your dataset size (e.g., try 5-10). We'll also compute the silhouette score to evaluate cluster quality (higher is better).

For visualization, we'll optionally reduce dimensions to 2D using UMAP.

In [ ]:
from umap import UMAP  # For 2D projection (optional)
import os
import numpy as np
import torch
import clip
from PIL import Image
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import warnings
warnings.filterwarnings('ignore')
# Choose number of clusters (experiment with this)
n_clusters = 5  # Adjust based on your data

# Perform K-Means clustering
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
cluster_labels = kmeans.fit_predict(embeddings)

# Evaluate clustering quality
sil_score = silhouette_score(embeddings, cluster_labels)
print(f"Silhouette Score: {sil_score:.3f} (closer to 1 is better)")

# Optional: 2D visualization with UMAP
reducer = UMAP(random_state=42, n_components=2)
embed_2d = reducer.fit_transform(embeddings)

plt.figure(figsize=(10, 8))
scatter = plt.scatter(embed_2d[:, 0], embed_2d[:, 1], c=cluster_labels, cmap='tab10', s=50)
plt.colorbar(scatter)
plt.title(f'2D UMAP Projection of CLIP Embeddings (K={n_clusters} Clusters)')
plt.xlabel('UMAP 1')
plt.ylabel('UMAP 2')
plt.show()

Sort Images into Clusters
This creates subdirectories for each cluster and moves/copies the images there. Set `move_files=True` to move (or False to copy).

In [ ]:
import shutil

# Create cluster directories
output_dir = '/content/clusters'  # Output base directory (change if needed)
os.makedirs(output_dir, exist_ok=True)

move_files = False  # Set to True to move files, False to copy

for i in range(n_clusters):
    cluster_dir = os.path.join(output_dir, f'cluster_{i}')
    os.makedirs(cluster_dir, exist_ok=True)

# Assign and sort images
for idx, label in enumerate(cluster_labels):
    src_path = image_names[idx]
    dst_path = os.path.join(output_dir, f'cluster_{label}', image_names[idx])
    if move_files:
        shutil.move(src_path, dst_path)
    else:
        shutil.copy2(src_path, dst_path)
    print(f"Assigned {image_names[idx]} to cluster_{label}")

print(f"Images sorted into {n_clusters} clusters in '{output_dir}'")

Visualize Sample Images per Cluster
Display a few sample images from each cluster to inspect the results.

In [ ]:
def display_cluster_samples(cluster_dir, n_samples=3):
    images = [f for f in os.listdir(cluster_dir) if f.lower().endswith(('.png', '.jpg', '.jpeg'))][:n_samples]
    if not images:
        print(f"No images in {cluster_dir}")
        return

    fig, axs = plt.subplots(1, len(images), figsize=(5 * len(images), 5))
    if len(images) == 1:
        axs = [axs]
    for j, img_file in enumerate(images):
        img_path = os.path.join(cluster_dir, img_file)
        img = Image.open(img_path)
        axs[j].imshow(img)
        axs[j].set_title(img_file)
        axs[j].axis('off')
    plt.show()

# Display samples from each cluster
for i in range(n_clusters):
    cluster_dir = os.path.join(output_dir, f'cluster_{i}')
    print(f"\nSamples from Cluster {i}:")
    display_cluster_samples(cluster_dir)

In [ ]:
#@markdown Upload to Google Drive as .zip folder (Be mindful of Google Drive Terms of Service)
drive_folder_name = 'my_zip_folder' # @param {type:'string'}

%cd /content/
!zip -r /content/drive/MyDrive/{drive_folder_name}.zip /content/clusters



Tips and Next Steps
- **Choosing `n_clusters`**: Run the clustering cell multiple times with different values and pick the one with the highest silhouette score. Alternatively, use elbow method or silhouette analysis for more advanced selection.
- **Alternative Clustering**: For density-based clustering (handles varying cluster sizes better), replace K-Means with HDBSCAN: `!pip install hdbscan` and use `from hdbscan import HDBSCAN; clusterer = HDBSCAN(min_cluster_size=5); cluster_labels = clusterer.fit_predict(embeddings)`.
- **Larger Datasets**: If you have thousands of images, batch the embedding extraction to avoid memory issues.
- **Custom Prompts**: CLIP is multimodal— you could refine clusters by comparing image embeddings to text prompts (e.g., `model.encode_text(clip.tokenize(["a photo of a dog", "a photo of a car"]))`).
- **Download Results**: Right-click the `/content/clusters` folder in the Colab file browser and download as ZIP.